In [1]:
import pandas as pd
import datetime as dt
import ast
import geopandas as gpd
import numpy as np
pd.options.display.float_format = "{:.2f}".format

In [2]:
hamilton = gpd.read_file('ham_2020_cbg.geojson')
hamilton['geoid20'] = hamilton['geoid20'].astype(float)

In [3]:
hamilton_cbgs = hamilton.geoid20.unique().tolist()

In [4]:
type(hamilton_cbgs[0])

float

In [5]:
safe_df =  pd.read_parquet('../Hamilton county/safegraph.parquet/year=2021/region=TN/city=Chattanooga/', engine='pyarrow')

In [6]:
safe_df.head()

brands                               bucketed_dwell_times category_tags  \
0    nan  {"<5":0,"5-10":1,"11-20":3,"21-60":2,"61-120":...       Gourmet   
1    nan  {"<5":0,"5-10":2,"11-20":1,"21-60":2,"61-120":...       Gourmet   
2    nan  {"<5":1,"5-10":6,"11-20":0,"21-60":6,"61-120":...       Gourmet   
3    nan  {"<5":0,"5-10":4,"11-20":4,"21-60":1,"61-120":...       Gourmet   
4    nan  {"<5":0,"5-10":4,"11-20":0,"21-60":1,"61-120":...       Gourmet   

  closed_on  date_begin    date_end             date_range_end  \
0       nan  2021-03-15  2021-03-22  2021-03-22T00:00:00-04:00   
1       nan  2021-12-27  2022-01-03  2022-01-03T00:00:00-05:00   
2       nan  2021-03-22  2021-03-29  2021-03-29T00:00:00-04:00   
3       nan  2021-02-22  2021-03-01  2021-03-01T00:00:00-05:00   
4       nan  2021-07-26  2021-08-02  2021-08-02T00:00:00-04:00   

            date_range_start  dayofmonth             device_type  ...  \
0  2021-03-15T00:00:00-04:00          15   {"android":4,"ios":0}  ...   
1  2021-12-27T00:00:00-05:00          27   {"android":4,"ios":4}  ...   
2  2021-03-22T00:00:00-04:00          22  {"android":4,"ios":10}  ...   
3  2021-02-22T00:00:00-05:00          22   {"android":4,"ios":6}  ...   
4  2021-07-26T00:00:00-04:00          26   {"android":4,"ios":0}  ...   

     visits_by_day                                visits_by_each_hour  \
0  [1,0,1,0,1,4,0]  [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0...   
1  [1,2,1,4,0,2,1]  [0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0...   
2  [1,2,2,3,4,1,0]  [0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0...   
3  [4,1,1,2,1,1,0]  [0,0,0,0,0,0,0,0,0,0,1,0,1,0,0,0,0,1,0,1,0,0,0...   
4  [0,1,3,0,0,3,1]  [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0...   

  visits_friday visits_monday visits_saturday visits_sunday  visits_thursday  \
0             1             1               4             0                0   
1             0             1               2             1                4   
2             4             1               1             0                3   
3             1             4               1             0                2   
4             0             0               3             1                0   

  visits_tuesday  visits_wednesday  wkt_area_sq_meters  
0              0                 1              120.00  
1              2                 1              120.00  
2              2                 2              120.00  
3              1                 1              120.00  
4              1                 3              120.00  

[5 rows x 59 columns]

In [7]:
# reference : # https://docs.safegraph.com/docs/places

safe_df.columns

Index(['brands', 'bucketed_dwell_times', 'category_tags', 'closed_on',
       'date_begin', 'date_end', 'date_range_end', 'date_range_start',
       'dayofmonth', 'device_type', 'distance_from_home', 'enclosed',
       'geometry_type', 'includes_parking_lot', 'is_synthetic',
       'iso_country_code', 'latitude', 'location_name', 'longitude',
       'median_dwell', 'month', 'naics_code',
       'normalized_visits_by_region_naics_visitors',
       'normalized_visits_by_region_naics_visits',
       'normalized_visits_by_state_scaling',
       'normalized_visits_by_total_visitors',
       'normalized_visits_by_total_visits', 'open_hours', 'opened_on',
       'parent_placekey', 'phone_number', 'placekey', 'poi_cbg',
       'polygon_class', 'polygon_wkt', 'postal_code', 'raw_visit_counts',
       'raw_visitor_counts', 'related_same_day_brand',
       'related_same_week_brand', 'safegraph_brand_ids', 'street_address',
       'sub_category', 'top_category', 'tracking_closed_since',
       'vi

In [10]:
l= ['category_tags', 'naics_code', 'date_begin','distance_from_home', 'includes_parking_lot','location_name', 'poi_cbg','open_hours','raw_visit_counts', 'related_same_day_brand','related_same_week_brand','sub_category', 'top_category','visits_by_day','visits_friday','visits_saturday', 'visits_sunday', 'visits_monday', 'visits_tuesday', 'visits_wednesday', 'visits_thursday', 'polygon_wkt']

In [11]:
df = safe_df.drop(safe_df.columns.difference(['visitor_home_aggregation', 'visitor_home_cbgs']+ l), 1)
df

c:\Users\senr1\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  """Entry point for launching an IPython kernel.


category_tags  date_begin  distance_from_home includes_parking_lot  \
0            Gourmet  2021-03-15            11535.00                false   
1            Gourmet  2021-12-27            16664.00                false   
2            Gourmet  2021-03-22            22979.00                false   
3            Gourmet  2021-02-22            10211.00                false   
4            Gourmet  2021-07-26            22243.00                false   
...              ...         ...                 ...                  ...   
227436   Auto Repair  2021-11-08           120677.00                false   
227437   Auto Repair  2021-01-11                 NaN                false   
227438   Auto Repair  2021-12-13                 NaN                false   
227439   Auto Repair  2021-11-01                 NaN                false   
227440   Auto Repair  2021-01-25                 NaN                false   

                        location_name  naics_code  \
0       Nature's Sunshine Distributor   446191.00   
1       Nature's Sunshine Distributor   446191.00   
2       Nature's Sunshine Distributor   446191.00   
3       Nature's Sunshine Distributor   446191.00   
4       Nature's Sunshine Distributor   446191.00   
...                               ...         ...   
227436                  City Radiator     8111.00   
227437                  City Radiator     8111.00   
227438                  City Radiator     8111.00   
227439                  City Radiator     8111.00   
227440                  City Radiator     8111.00   

                                               open_hours         poi_cbg  \
0       { "Mon": [["9:00", "18:00"]], "Tue": [["9:00",... 470650114431.00   
1       { "Mon": [["9:00", "18:00"]], "Tue": [["9:00",... 470650114431.00   
2       { "Mon": [["9:00", "18:00"]], "Tue": [["9:00",... 470650114431.00   
3       { "Mon": [["9:00", "18:00"]], "Tue": [["9:00",... 470650114431.00   
4       { "Mon": [["9:00", "18:00"]], "Tue": [["9:00",... 470650114431.00   
...                                                   ...             ...   
227436  { "Mon": [["8:00", "17:00"]], "Tue": [["8:00",... 470650023001.00   
227437  { "Mon": [["8:00", "17:00"]], "Tue": [["8:00",... 470650023001.00   
227438  { "Mon": [["8:00", "17:00"]], "Tue": [["8:00",... 470650023001.00   
227439  { "Mon": [["8:00", "17:00"]], "Tue": [["8:00",... 470650023001.00   
227440  { "Mon": [["8:00", "17:00"]], "Tue": [["8:00",... 470650023001.00   

                                              polygon_wkt  raw_visit_counts  \
0       POLYGON ((-85.15037442716003 35.05151565896911...              7.00   
1       POLYGON ((-85.15037442716003 35.05151565896911...             11.00   
2       POLYGON ((-85.15037442716003 35.05151565896911...             13.00   
3       POLYGON ((-85.15037442716003 35.05151565896911...             10.00   
4       POLYGON ((-85.15037442716003 35.05151565896911...              8.00   
...                                                   ...               ...   
227436  POLYGON ((-85.28913457699997 34.98644406600005...             24.00   
227437  POLYGON ((-85.28913457699997 34.98644406600005...              2.00   
227438  POLYGON ((-85.28913457699997 34.98644406600005...             12.00   
227439  POLYGON ((-85.28913457699997 34.98644406600005...             17.00   
227440  POLYGON ((-85.28913457699997 34.98644406600005...              3.00   

        ...                           visitor_home_aggregation  \
0       ...                                  {"13047030202":4}   
1       ...                                  {"47065010432":4}   
2       ...                  {"47065011204":4,"47011011300":4}   
3       ...  {"47011011601":4,"47065011447":4,"13047030202":4}   
4       ...                                                 {}   
...     ...                                                ...   
227436  ...  {"13313000200":4,"47065010800":4,"47013950100":4}   
227437  ...                                

In [12]:
df['poi_cbg'] = df['poi_cbg'].astype(float)
df = df[df['poi_cbg'].isin(hamilton_cbgs)].reset_index(drop = True)

In [13]:
#pd.DataFrame(data=df.loc[9,l]).T

In [14]:
df['visitor_home_cbgs'] = pd.DataFrame(df['visitor_home_cbgs'].apply(ast.literal_eval))

In [15]:
def func(x):
    return pd.DataFrame(x.items(), columns = ['home_cbg','frequency'])

In [16]:
df['visitor_info'] = df.apply(lambda x: func(x['visitor_home_cbgs']), axis =1)

In [17]:
df = df.sort_values(by = ['date_begin']).reset_index(drop = True)
df

category_tags  date_begin  \
0                                   Roofing,Waterproofing  2021-01-04   
1                                            Mexican Food  2021-01-04   
2                                                     nan  2021-01-04   
3                                     Children's Clothing  2021-01-04   
4                               Buffet,Chinese Food,Sushi  2021-01-04   
...                                                   ...         ...   
205563                 Ophthalmologists,Retina Specialist  2021-12-27   
205564                          Data Recovery,IT Services  2021-12-27   
205565  Bar or Pub,Brewery or Brewpub,Cocktail Lounge,...  2021-12-27   
205566                                Cannabis Dispensary  2021-12-27   
205567  Churches,Hindu Temple,Mosque,Sikh Temple,Synag...  2021-12-27   

        distance_from_home includes_parking_lot  \
0                 50442.00                false   
1                 11500.00                false   
2                 25710.00                false   
3                      NaN                false   
4                 18774.00                false   
...                    ...                  ...   
205563             9049.00                false   
205564            16868.00                false   
205565           152502.00                false   
205566            15378.00                false   
205567             4809.00                false   

                                  location_name  naics_code  \
0                 Tri State Roofing Contractors     2383.00   
1                          El Meson Restaurante   722511.00   
2       Milligan Reynolds Guaranty Title Agency   524210.00   
3                     A Child's Garden Boutique     4481.00   
4                               Chef Lin Buffet   722511.00   
...                                         ...         ...   
205563           Southeastern Retina Associates   621111.00   
205564                              Data Recoup   811211.00   
205565                       Gate 11 Distillery   312140.00   
205566                          Snapdragon Hemp   446110.00   
205567                                  St Mary   813110.00   

                                               open_hours         poi_cbg  \
0                                                     nan 470650019002.00   
1                                                     nan 470650104321.00   
2       { "Mon": [["8:30", "17:00"]], "Tue": [["8:30",... 470650031001.00   
3       { "Mon": [["12:30", "18:00"]], "Tue": [["12:30... 470650006001.00   
4       { "Mon": [["11:00", "22:00"]], "Tue": [["11:00... 470650116002.00   
...                                                   ...             ...   
205563  { "Mon": [["8:00", "16:00"]], "Tue": [["8:00",... 470650104334.00   
205564                                                nan 470650104334.00   
205565  { "Mon": [], "Tue": [], "Wed": [["10:00", "20:... 470650124003.00   
205566  { "Mon": [["11:00", "20:00"]], "Tue": [["11:00... 470650104321.00   
205567                                                nan 470650122001.00   

                                              polygon_wkt  raw_visit_counts  \
0       POLYGON ((-85.31093239499995 35.01642522600002...             68.00   
1       POLYGON ((-85.23887732568659 35.13297318389888...             80.00   
2       POLYGON ((-85.30795771299995 35.04749844500003...              6.00   
3       POLYGON ((-85.30667786599997 35.06265751700005...              2.00   
4       POLYGON ((-85.22243095599998 35.00271018800004...             24.00   
...                                                   ...               ...   
205563  POLYGON ((-85.24631671899994 35.12534650500004...             34.00   
205564  POLYGON ((-85.24205880049499 35.12599955709304...            103.00   
205565  POLYGON ((-85.30426024699995 35.03723169900007...            166.00   
205566  POLYGON ((-85.23728651499994 35.12105816900004...              6.00   
205

In [18]:
# grp = df.groupby(['date_begin', 'category_tags', 'distance_from_home', 'includes_parking_lot', 'location_name', 'open_hours', 'raw_visit_counts', 'related_same_day_brand', 'related_same_week_brand', 'sub_category', 'top_category', 'visits_by_day', 'visits_friday','visits_monday', 'visits_saturday', 'visits_sunday', 'visits_thursday', 'visits_tuesday', 'visits_wednesday', 'polygon_wkt', 'home_cbg', 'poi_cbg']).agg({'frequency': sum}).reset_index()
df['visitor_info']

0                home_cbg  frequency
0  471079708001    ...
1                home_cbg  frequency
0  470650103043    ...
2         Empty DataFrame
Columns: [home_cbg, frequency]...
3         Empty DataFrame
Columns: [home_cbg, frequency]...
4                home_cbg  frequency
0  130470302012    ...
                                ...                        
205563    Empty DataFrame
Columns: [home_cbg, frequency]...
205564            home_cbg  frequency
0   470650114021  ...
205565            home_cbg  frequency
0   470650106002  ...
205566           home_cbg  frequency
0  470650112014    ...
205567           home_cbg  frequency
0  470650104124    ...
Name: visitor_info, Length: 205568, dtype: object

In [19]:
chunks = np.array_split(df, 5)

In [20]:
t = [chunks[i].groupby('date_begin') for i in range(5)]

In [21]:
# for key in t[0].groups:
#     x = t[0].get_group(key)
#     print(x)

In [22]:
x = t[0].get_group(dt.date(2021, 1, 4))

In [107]:
sanity check

# y = pd.DataFrame()
# for i in range(len(x)):
#     temp = x['visitor_info'][i]
#     alpha = pd.DataFrame(data=df.loc[i,l]).T
#     temp = pd.concat([temp,alpha], axis = 1)   
#     print(temp)

       home_cbg  frequency          category_tags  date_begin  \
0  471079708001          4  Roofing,Waterproofing  2021-01-04   
1  470650019002          4                    NaN         NaN   
2  470110111001          4                    NaN         NaN   
3  010730114002          4                    NaN         NaN   
4  130470306004          4                    NaN         NaN   
5  470650026001          4                    NaN         NaN   

  distance_from_home includes_parking_lot                  location_name  \
0           50442.00                false  Tri State Roofing Contractors   
1                NaN                  NaN                            NaN   
2                NaN                  NaN                            NaN   
3                NaN                  NaN                            NaN   
4                NaN                  NaN                            NaN   
5                NaN                  NaN                            NaN   

          p

: 

: 

In [52]:
# t[0].get_group(key)
key

datetime.date(2021, 3, 15)

In [23]:
# y

In [24]:
res = pd.DataFrame()

for key in t[0].groups:
    x = t[0].get_group(key)
    x = x.reset_index(drop = True)
    y = pd.DataFrame()
    for i in range(len(x)):
        temp = x['visitor_info'][i]
        # print(temp)
        alpha = pd.DataFrame(data=df.loc[i,l]).T
        temp = pd.concat([temp,alpha], axis = 1) 
        temp['date_begin'] = x['date_begin'][i]
        temp['poi_cbg'] = x['poi_cbg'][i]
        temp['category_tags'] = x['category_tags'][i]
        temp['naics_code'] = x['naics_code'][i]
        temp['distance_from_home'] = x['distance_from_home'][i]
        temp['includes_parking_lot'] = x['includes_parking_lot'][i]
        temp['location_name'] = x['location_name'][i]
        temp['open_hours'] = x['open_hours'][i]
        temp['raw_visit_counts'] = x['raw_visit_counts'][i]
        temp['related_same_day_brand'] = x['related_same_day_brand'][i]
        temp['related_same_week_brand'] = x['related_same_week_brand'][i]
        temp['sub_category'] = x['sub_category'][i]
        temp['top_category'] = x['top_category'][i]
        temp['visits_by_day'] = x['visits_by_day'][i]
        temp['visits_monday'] = x['visits_monday'][i]
        temp['visits_tuesday'] = x['visits_tuesday'][i]
        temp['visits_wednesday'] = x['visits_wednesday'][i]
        temp['visits_thursday'] = x['visits_thursday'][i]
        temp['visits_friday'] = x['visits_friday'][i]
        temp['visits_saturday'] = x['visits_saturday'][i]
        temp['visits_sunday'] = x['visits_sunday'][i]
        temp['polygon_wkt'] = x['polygon_wkt'][i]
        y = y.append(temp)
    y['home_cbg'] = pd.to_numeric(y['home_cbg'], errors='coerce')
    y = y.dropna(subset=['home_cbg'])
    y['home_cbg'] =y['home_cbg'].astype(float)
    y = y[y['home_cbg'].isin(hamilton_cbgs)].reset_index(drop = True)
    y = y.groupby(['date_begin', 'category_tags', 'naics_code', 'distance_from_home', 'includes_parking_lot', 'location_name', 'open_hours', 'raw_visit_counts', 'related_same_day_brand', 'related_same_week_brand', 'sub_category', 'top_category', 'visits_by_day', 'visits_friday','visits_monday', 'visits_saturday', 'visits_sunday', 'visits_thursday', 'visits_tuesday', 'visits_wednesday', 'polygon_wkt', 'home_cbg', 'poi_cbg']).agg({'frequency': sum}).reset_index()
    res = res.append(y)
    res = res.reset_index(drop = True)

In [38]:
res

date_begin                                      category_tags  \
0       2021-01-04  3D Printing,Carpenters,Electronics,Fabrics,Ind...   
1       2021-01-04  3D Printing,Carpenters,Electronics,Fabrics,Ind...   
2       2021-01-04  3D Printing,Carpenters,Electronics,Fabrics,Ind...   
3       2021-01-04  3D Printing,Carpenters,Electronics,Fabrics,Ind...   
4       2021-01-04  3D Printing,Carpenters,Electronics,Fabrics,Ind...   
...            ...                                                ...   
188541  2021-03-15                                                nan   
188542  2021-03-15                                                nan   
188543  2021-03-15                                                nan   
188544  2021-03-15                                                nan   
188545  2021-03-15                                                nan   

        naics_code  distance_from_home includes_parking_lot  \
0          3399.00            10016.00                 true   
1          3399.00            10016.00                 true   
2          3399.00            10016.00                 true   
3          3399.00            10016.00                 true   
4          3399.00            10016.00                 true   
...            ...                 ...                  ...   
188541   926120.00            21284.00                false   
188542   926120.00            21284.00                false   
188543   926120.00            21284.00                false   
188544   926120.00            21284.00                false   
188545   926120.00            21284.00                false   

                 location_name open_hours  raw_visit_counts  \
0                          Amt        nan            145.00   
1                          Amt        nan            145.00   
2                          Amt        nan            145.00   
3                          Amt        nan            145.00   
4                          Amt        nan            145.00   
...                        ...        ...               ...   
188541  Chattanooga Street Art        nan             83.00   
188542  Chattanooga Street Art        nan             83.00   
188543  Chattanooga Street Art        nan             83.00   
188544  Chattanooga Street Art        nan             83.00   
188545  Chattanooga Street Art        nan             83.00   

                                   related_same_day_brand  \
0       {"Mapco":7,"Starbucks":7,"Walmart":6,"RaceWay"...   
1       {"Mapco":7,"Starbucks":7,"Walmart":6,"RaceWay"...   
2       {"Mapco":7,"Starbucks":7,"Walmart":6,"RaceWay"...   
3       {"Mapco":7,"Starbucks":7,"Walmart":6,"RaceWay"...   
4       {"Mapco":7,"Starbucks":7,"Walmart":6,"RaceWay"...   
...                                                   ...   
188541  {"Staybridge Suites":11,"Walmart":5,"Taco Bell...   
188542  {"Staybridge Suites":11,"Walmart":5,"Taco Bell...   
188543  {"Staybridge Suites":11,"Walmart":5,"Taco Bell...   
188544  {"Staybridge Suites":11,"Walmart":5,"Taco Bell...   
188545  {"Staybridge Suites":11,"Walmart":5,"Taco Bell...   

                                  related_same_week_brand  ... visits_monday  \
0       {"Walmart":23,"Starbucks":17,"Mapco":15,"Circl...  ...            26   
1       {"Walmart":23,"Starbucks":17,"Mapco":15,"Circl...  ...            26   
2       {"Walmart":23,"Starbucks":17,"Mapco":15,"Circl...  ...            26   
3       {"Walmart":23,"Starbucks":17,"Mapco":15,"Circl...  ...            26   
4       {"Walmart":23,"Starbucks":17,"Mapco":15,"Circl...  ...            26   
...                                                   ...  ...           ...   
188541  {"Walmart":24,"Chick-fil-A":24,"Taco Bell":22,...  ...            13   
188542  {"Walmart":24,"Chick-fil-A":24,"Taco Bell":22,...  ...            13   
188543  {"Walmart":24,"Chick-fil-A":24,"Taco Bell":22,...  ...            13   
188544  {"Walmart":24,"Chick-fil-A":24,"Taco Bell":22,...  ...            13   
1885

In [37]:
from datetime import datetime
start_date = datetime.strptime('Jan 11 2021  11:59PM', '%b %d %Y %I:%M%p').date()
end_date = datetime.strptime('Jan 17 2021  11:59AM', '%b %d %Y %I:%M%p').date()
# end_date
exact_date = datetime.strptime('Jan 11 2021  12:00AM', '%b %d %Y %I:%M%p').date()

res2 = res
res2.home_cbg = res2.home_cbg.astype('double') 
res2.home_cbg = res2.home_cbg.astype('int64') 
res2.home_cbg = res2.home_cbg.astype('str') 

res2[res2.date_begin==exact_date].reset_index(drop=True)
res3 = res2.merge(ham_cbg[['TRACTCE', 'GEOID', 'NAMELSAD', 'geometry']], left_on='home_cbg', right_on='GEOID').drop('GEOID', axis=1)

res3.to_csv('ham_safegraph_week2_jan2021.csv', index=False)

In [44]:
res2.drop('polygon_wkt', axis=1).to_csv('ham_sg_week2_jan21.csv')

In [62]:
for key in t[1].groups:
    x = t[1].get_group(key)
    x = x.reset_index(drop = True)
    y = pd.DataFrame()
    for i in range(len(x)):
        temp = x['visitor_info'][i]
        temp['date_begin'] = x['date_begin'][i]
        temp['poi_cbg'] = x['poi_cbg'][i]
        temp['category_tags'] = x['category_tags'][i]
        temp['distance_from_home'] = x['distance_from_home'][i]
        temp['includes_parking_lot'] = x['includes_parking_lot'][i]
        temp['location_name'] = x['location_name'][i]
        temp['open_hours'] = x['open_hours'][i]
        temp['raw_visit_counts'] = x['raw_visit_counts'][i]
        temp['related_same_day_brand'] = x['related_same_day_brand'][i]
        temp['related_same_week_brand'] = x['related_same_week_brand'][i]
        temp['sub_category'] = x['sub_category'][i]
        temp['top_category'] = x['top_category'][i]
        temp['visits_by_day'] = x['visits_by_day'][i]
        temp['visits_monday'] = x['visits_monday'][i]
        temp['visits_tuesday'] = x['visits_tuesday'][i]
        temp['visits_wednesday'] = x['visits_wednesday'][i]
        temp['visits_thursday'] = x['visits_thursday'][i]
        temp['visits_friday'] = x['visits_friday'][i]
        temp['visits_saturday'] = x['visits_saturday'][i]
        temp['visits_sunday'] = x['visits_sunday'][i]
        temp['polygon_wkt'] = x['polygon_wkt'][i]
        y = y.append(temp)
    y['home_cbg'] = pd.to_numeric(y['home_cbg'], errors='coerce')
    y = y.dropna(subset=['home_cbg'])
    y['home_cbg'] =y['home_cbg'].astype(float)
    y = y[y['home_cbg'].isin(hamilton_cbgs)].reset_index(drop = True)
    y = y.groupby(['date_begin', 'category_tags', 'home_cbg', 'poi_cbg']).agg({'frequency': sum}).reset_index()
    res = res.append(y)
    res = res.reset_index(drop = True)

In [66]:
for key in t[2].groups:
    x = t[2].get_group(key)
    x = x.reset_index(drop = True)
    y = pd.DataFrame()
    for i in range(len(x)):
        temp = x['visitor_info'][i]
        temp['date_begin'] = x['date_begin'][i]
        temp['poi_cbg'] = x['poi_cbg'][i]
        # temp['brands'] = x['brands'][i]
        temp['category_tags'] = x['category_tags'][i]
        temp['distance_from_home'] = x['distance_from_home'][i]
        temp['includes_parking_lot'] = x['includes_parking_lot'][i]
        temp['location_name'] = x['location_name'][i]
        temp['open_hours'] = x['open_hours'][i]
        temp['raw_visit_counts'] = x['raw_visit_counts'][i]
        temp['related_same_day_brand'] = x['related_same_day_brand'][i]
        temp['related_same_week_brand'] = x['related_same_week_brand'][i]
        temp['sub_category'] = x['sub_category'][i]
        temp['top_category'] = x['top_category'][i]
        temp['visits_by_day'] = x['visits_by_day'][i]
        temp['visits_monday'] = x['visits_monday'][i]
        temp['visits_tuesday'] = x['visits_tuesday'][i]
        temp['visits_wednesday'] = x['visits_wednesday'][i]
        temp['visits_thursday'] = x['visits_thursday'][i]
        temp['visits_friday'] = x['visits_friday'][i]
        temp['visits_saturday'] = x['visits_saturday'][i]
        temp['visits_sunday'] = x['visits_sunday'][i]
        temp['polygon_wkt'] = x['polygon_wkt'][i]
        y = y.append(temp)
    y['home_cbg'] = pd.to_numeric(y['home_cbg'], errors='coerce')
    y = y.dropna(subset=['home_cbg'])
    y['home_cbg'] =y['home_cbg'].astype(float)
    y = y[y['home_cbg'].isin(hamilton_cbgs)].reset_index(drop = True)
    y = y.groupby(['date_begin', 'category_tags', 'distance_from_home', 'includes_parking_lot', 'location_name', 'open_hours', 'raw_visit_counts', 'related_same_day_brand', 'related_same_week_brand', 'sub_category', 'top_category', 'visits_by_day', 'visits_friday','visits_monday', 'visits_saturday', 'visits_sunday', 'visits_thursday', 'visits_tuesday', 'visits_wednesday', 'polygon_wkt', 'home_cbg', 'poi_cbg']).agg({'frequency': sum}).reset_index()
    res = res.append(y)
    res = res.reset_index(drop = True)

In [68]:
for key in t[3].groups:
    x = t[3].get_group(key)
    x = x.reset_index(drop = True)
    y = pd.DataFrame()
    for i in range(len(x)):
        temp = x['visitor_info'][i]
        temp['date_begin'] = x['date_begin'][i]
        temp['poi_cbg'] = x['poi_cbg'][i]
        temp['category_tags'] = x['category_tags'][i]
        temp['distance_from_home'] = x['distance_from_home'][i]
        temp['includes_parking_lot'] = x['includes_parking_lot'][i]
        temp['location_name'] = x['location_name'][i]
        temp['open_hours'] = x['open_hours'][i]
        temp['raw_visit_counts'] = x['raw_visit_counts'][i]
        temp['related_same_day_brand'] = x['related_same_day_brand'][i]
        temp['related_same_week_brand'] = x['related_same_week_brand'][i]
        temp['sub_category'] = x['sub_category'][i]
        temp['top_category'] = x['top_category'][i]
        temp['visits_by_day'] = x['visits_by_day'][i]
        temp['visits_monday'] = x['visits_monday'][i]
        temp['visits_tuesday'] = x['visits_tuesday'][i]
        temp['visits_wednesday'] = x['visits_wednesday'][i]
        temp['visits_thursday'] = x['visits_thursday'][i]
        temp['visits_friday'] = x['visits_friday'][i]
        temp['visits_saturday'] = x['visits_saturday'][i]
        temp['visits_sunday'] = x['visits_sunday'][i]
        temp['polygon_wkt'] = x['polygon_wkt'][i]
        y = y.append(temp)
    y['home_cbg'] = pd.to_numeric(y['home_cbg'], errors='coerce')
    y = y.dropna(subset=['home_cbg'])
    y['home_cbg'] =y['home_cbg'].astype(float)
    y = y[y['home_cbg'].isin(hamilton_cbgs)].reset_index(drop = True)
    y = y.groupby(['date_begin', 'category_tags', 'distance_from_home', 'includes_parking_lot', 'location_name', 'open_hours', 'raw_visit_counts', 'related_same_day_brand', 'related_same_week_brand', 'sub_category', 'top_category', 'visits_by_day', 'visits_friday','visits_monday', 'visits_saturday', 'visits_sunday', 'visits_thursday', 'visits_tuesday', 'visits_wednesday', 'polygon_wkt', 'home_cbg', 'poi_cbg']).agg({'frequency': sum}).reset_index()
    res = res.append(y)
    res = res.reset_index(drop = True)

In [69]:
for key in t[4].groups:
    x = t[4].get_group(key)
    x = x.reset_index(drop = True)
    y = pd.DataFrame()
    for i in range(len(x)):
        temp = x['visitor_info'][i]
        temp['date_begin'] = x['date_begin'][i]
        temp['poi_cbg'] = x['poi_cbg'][i]
        # temp['brands'] = x['brands'][i]
        temp['category_tags'] = x['category_tags'][i]
        temp['distance_from_home'] = x['distance_from_home'][i]
        temp['includes_parking_lot'] = x['includes_parking_lot'][i]
        temp['location_name'] = x['location_name'][i]
        temp['open_hours'] = x['open_hours'][i]
        temp['raw_visit_counts'] = x['raw_visit_counts'][i]
        temp['related_same_day_brand'] = x['related_same_day_brand'][i]
        temp['related_same_week_brand'] = x['related_same_week_brand'][i]
        temp['sub_category'] = x['sub_category'][i]
        temp['top_category'] = x['top_category'][i]
        temp['visits_by_day'] = x['visits_by_day'][i]
        temp['visits_monday'] = x['visits_monday'][i]
        temp['visits_tuesday'] = x['visits_tuesday'][i]
        temp['visits_wednesday'] = x['visits_wednesday'][i]
        temp['visits_thursday'] = x['visits_thursday'][i]
        temp['visits_friday'] = x['visits_friday'][i]
        temp['visits_saturday'] = x['visits_saturday'][i]
        temp['visits_sunday'] = x['visits_sunday'][i]
        temp['polygon_wkt'] = x['polygon_wkt'][i]
        y = y.append(temp)
    y['home_cbg'] = pd.to_numeric(y['home_cbg'], errors='coerce')
    y = y.dropna(subset=['home_cbg'])
    y['home_cbg'] =y['home_cbg'].astype(float)
    y = y[y['home_cbg'].isin(hamilton_cbgs)].reset_index(drop = True)
    y = y.groupby(['date_begin', 'category_tags', 'distance_from_home', 'includes_parking_lot', 'location_name', 'open_hours', 'raw_visit_counts', 'related_same_day_brand', 'related_same_week_brand', 'sub_category', 'top_category', 'visits_by_day', 'visits_friday','visits_monday', 'visits_saturday', 'visits_sunday', 'visits_thursday', 'visits_tuesday', 'visits_wednesday', 'polygon_wkt', 'home_cbg', 'poi_cbg']).agg({'frequency': sum}).reset_index()
    res = res.append(y)
    res = res.reset_index(drop = True)

In [71]:
res.to_csv("hamilton_allweeks2021_new.csv")

In [36]:
ham_cbg = gpd.read_file('../Tennessee Census Block Groups/tl_2020_47_bg.shp')

In [105]:
res2 = res
res2.home_cbg = res2.home_cbg.astype('double') 
res2.home_cbg = res2.home_cbg.astype('int64') 
res2.home_cbg = res2.home_cbg.astype('str') 

In [130]:
res3 = res2.merge(ham_cbg[['TRACTCE', 'GEOID', 'NAMELSAD', 'geometry']], left_on='home_cbg', right_on='GEOID').drop('GEOID', axis=1)

In [132]:
res3.to_csv('hamilton_allweeks2021_cbg_names.csv', index=False)

In [136]:
res3[res3.date_begin<'2021-02-01']

date_begin                                      category_tags  \
0        2021-01-04  3D Printing,Carpenters,Electronics,Fabrics,Ind...   
1        2021-01-04  Arts and Crafts,Men's Clothing,Children's Clot...   
2        2021-01-04  Bar or Pub,Cocktail Lounge,Late Night,Mexican ...   
3        2021-01-04  Building Supplies,Flooring,Appliances,Hardware...   
4        2021-01-04                                           Car Wash   
...             ...                                                ...   
1009006  2021-01-04                                         Industrial   
1009007  2021-01-11                                         Industrial   
1009008  2021-01-18                                         Industrial   
1009009  2021-01-18  Lunch,Steak House,American Food,Casual Dining,...   
1009010  2021-01-25                                        Trophy Shop   

         distance_from_home includes_parking_lot  \
0                  10016.00                 True   
1                   8323.00                False   
2                  12204.00                False   
3                  11218.00                False   
4                   4707.00                False   
...                     ...                  ...   
1009006            30519.00                 True   
1009007            39137.00                 True   
1009008            33435.00                 True   
1009009            15790.00                False   
1009010             7153.00                False   

                                    location_name  \
0                                             Amt   
1                             Walmart Supercenter   
2                         Mezcla Cocina Y Cantina   
3                                          Lowe's   
4        Exquisite Hand Car Wash & Detail Shop II   
...                                           ...   
1009006    Chattanooga Metropolitan Airport Solar   
1009007    Chattanooga Metropolitan Airport Solar   
1009008    Chattanooga Metropolitan Airport Solar   
1009009                         Logan's Roadhouse   
1009010                               T & A Darts   

                                                open_hours  raw_visit_counts  \
0                                                      NaN            145.00   
1                                                      NaN           1212.00   
2                                                      NaN             60.00   
3        { "Mon": [["6:00", "21:00"]], "Tue": [["6:00",...            755.00   
4                                                      NaN             16.00   
...                                                    ...               ...   
1009006                                                NaN            962.00   
1009007                                                NaN            961.00   
1009008                                                NaN            774.00   
1009009  { "Mon": [["11:00", "22:00"]], "Tue": [["11:00...            156.00   
1009010                                                NaN             50.00   

                                    related_same_day_brand  \
0        {"Mapco":7,"Starbucks":7,"Walmart":6,"RaceWay"...   
1        {"Murphy USA":4,"RaceWay":4,"Starbucks":3,"Foo...   
2        {"Walmart":9,"Walgreens":7,"McDonald's":7,"Exx...   
3        {"Walmart":11,"The Home Depot":7,"Circle K":5,...   
4        {"Cook Out":19,"Popeyes Louisiana Kitchen":19,...   
...                                                    ...   
1009006  {"Walmart":4,"Chick-fil-A":4,"McDonald's":4,"S...   
1009007  {"Walmart":7,"Chick-fil-A":4,"McDonald's":4,"P...   
1009008  {"Walmart":5,"Chick-fil-A":4,"Starbucks":3,"P....   
1009009  {"Walmart":12,"Circle K Gas":6,"Circle K":5,"C...   
1009010  {"Walmart":11,"McDonald's":6,"Target":4,"Dolla...   

                                   related_same_week_brand  \
0        {"Walmart":23,"Starbucks":17,"Mapco":15,"Circl...   
1        {"McDonald's":16,"D

In [127]:
pd.set_option('display.max_columns', None)
location_df = pd.DataFrame(res3.location_name.unique(), columns=['locations']).sort_values('locations')
# .to_csv('locations.csv', index=False)
location_df.merge(res3[['location_name', 'category_tags']], left_on='locations', right_on='location_name', how='left')


locations location_name                    category_tags
0        1885 Grill    1885 Grill     American Food,Brunch,Seafood
1        1885 Grill    1885 Grill     American Food,Brunch,Seafood
2        1885 Grill    1885 Grill     American Food,Brunch,Seafood
3        1885 Grill    1885 Grill     American Food,Brunch,Seafood
4        1885 Grill    1885 Grill     American Food,Brunch,Seafood
...             ...           ...                              ...
1009054         NaN           NaN           Jewelry,Jewelry Repair
1009055         NaN           NaN                      Trophy Shop
1009056         NaN           NaN                       Industrial
1009057         NaN           NaN                              NaN
1009058         NaN           NaN  Car Wash,Coffee Shop,Deli,Diner

[1009059 rows x 3 columns]

In [33]:
res['category_tags'].value_counts().nlargest(20)

nan                                                                                                         215191
Arts and Crafts,Men's Clothing,Children's Clothing,Home Décor,Baby Supplies                                  29054
Counter Service,Lunch,Fast Food,Drive Through,Breakfast,Dinner,Burgers                                       27968
Medical Supplies                                                                                             14504
Dialysis,Hospice,Physical Therapy,Walk-in Clinic                                                             11372
Mexican Food                                                                                                 11289
Snacks,Counter Service,Dessert,Tea House,Coffee Shop,Bakery                                                  10875
Commercial Real Estate,Property Management                                                                   10189
Counter Service,Late Night,Lunch,Fast Food,Drive Through,Breakfast,Dinner,Burger

In [45]:
sample = safe_df.sample(n = 50)
sample.to_csv("sample.csv")